# Goal : Scan the 3D predcitions of the FP with the Dpo fold database. 

### A. Run Foldseek
### B. Get the hits with good proba
### C. Report the folds
***

In [ ]:

rsync -avzhe ssh \
conchae@garnatxa.srv.cpd:/home/conchae/PhageDepo_pdb/benchmarking \
/media/concha-eloko/Linux/PhageDEPOdetection/ 


# A

In [2]:
import subprocess
import os

path_project = "/media/concha-eloko/Linux/PhageDEPOdetection"
path_pdb = f"{path_project}/FN_pdb"

for file in os.listdir(path_pdb) :
    if file.count("|") > 0 :
        file_name = file.split("|")[1].split(".pdb")[0]
        print(file_name)
        os.rename(f"{path_pdb}/{file}", f"{path_pdb}/{file_name}.pdb")

GU323708.1_prot_ADA79897.1_17
HG799496.1_prot_CDL73970.1_7
HG799497.1_prot_CDL74024.1_7
KC700556.1_prot_AGM12047.1_24
FR671406.1_prot_CBW38974.1_7


In [ ]:
import subprocess
import os

path_project = "/media/concha-eloko/Linux/PhageDEPOdetection"
path_pdb = f"{path_project}/FP_pdb"
path_db = f"/media/concha-eloko/Linux/depolymerase_building/RefDepo_domains/RefDepo_domains_db"
path_tmp = f"{path_project}/tmp"

def seek_beta_helix(path_in) :
    dir_out = f"{path_project}/FP_foldseek"
    protein_id = path_in.split("/")[-1].split(".pdb")[0].split("'")[1]
    path_out = f"{dir_out}/{protein_id}.out"
    output_frmt = f"query,target,pident,alnlen,gapopen,qstart,qend,tstart,tend,bits,prob"
    seek = f"foldseek easy-search {path_in} {path_db} {path_out} {path_tmp} --format-output {output_frmt}"
    print(seek)
    #seek = f"foldseek easy-search {path_in} {path_db} {path_out}.html {path_tmp} --format-mode 3"
    seek_process = subprocess.Popen(seek, shell=True, stdout=subprocess.PIPE, stderr=subprocess.STDOUT)
    press_out, press_err = seek_process.communicate()
    print (press_out, press_err)

paths = [f"{path_pdb}/'{file}'" for file in os.listdir(f"{path_pdb}") if file[-3:]=="pdb"]

for path in paths :
    seek_beta_helix(path)

***
## B  

> Get a list of the failed Dpos

In [1]:
import pandas as pd
import os 

path_project = "/media/concha-eloko/Linux/PhageDEPOdetection"
dir_out = f"{path_project}/FP_foldseek"

path_info = f"/media/concha-eloko/Linux/depolymerase_building/depolymerase_fold.csv"
info_df = pd.read_csv(path_info , sep = "\t", header = 0)

FP_results = {}
no_structure = []
outputs = [f"{dir_out}/{file}" for file in os.listdir(dir_out) if file[-3:]=="out"]
header_seekfold = ["query","target","pident","alnlen","gapopen","qstart","qend","tstart","tend","bits","prob"]

for results in outputs :
    results_df = pd.read_csv(f"{results}", sep = "\t" , names = header_seekfold)
    for _,row in results_df.iterrows() :
        fold = info_df[info_df["ID"] == row["target"]]["X_Group_Name"].values[0]
        if fold != "jelly-roll" :
            if row["prob"] >= 0.2 :
                FP_results[row["query"]]= (row["prob"],row["target"] , fold)
                break
    else :
        no_structure.append(row["query"])
                


In [6]:
def view_pdb(file) : 
    view = nv.show_structure_file(file , ext="pdb" , gui=False)
    #view.add_label("position")
    #view.add_label("res")
    return view

n = 0

In [14]:
path_project = "/media/concha-eloko/Linux/PhageDEPOdetection/FN_pdb"
import nglview as nv
import os
for i, file in enumerate(os.listdir(path_project)) :
    if i == n and file != "Dpos_reference.T12_FN.3L.2107.multi.fasta":
        view = view_pdb(f"{path_project}/{file}")
        #view.render_image(trim=True)
        print(file)
        n += 1 
        break
view

KC700557.1_prot_AGM12123.1_25.pdb


NGLWidget()